## Embedding
이러한 One-hot-Encoding은 하나의 원소만 1이고 나머지의 원소는 0이므로 Sparse하다고 표현된다.  
이러한 Sparse한 표현 형태를 Dense한 **임베딩 행렬**을 곱하는 행위  
이러한 Dense한 Embedding은 다음과 같은 3가지의 장점을 가지게 된다.  
1. 데이터의 표현 형태를 Sparse한 형태에서 Dense한 형태로 바꿔서더욱 효율적인 학습이 가능하도록 만들어 준다.
2. 데이터의 차원을 축소해서 연산량을 감소시킨다.
3. 단어 사이의 유사성을 표현할 수 있다.

텐서플로와 numpy 라이브러리를 임포트

In [2]:
import tensorflow as tf
import numpy as np

원본 데이터의 전체 단어 개수(One-hot-Encoding 표현의 차원)와 축소 할 임베딩 차원을 정의

In [3]:
vocab_size = 100 # One-hot-encoding 된 vocab 크기
embedding_size = 25 # 임베딩된 vocab 크기

스칼라 형태의 One-hot-Encoding 인풋 데이터를 받기 위한 플레이스홀더를 정의

In [4]:
inputs = tf.placeholder(tf.int32, shape=[None])

임베딩 행렬은 선언하고 tf.nn.embedding_lookup API를 이용해서 임베딩을 수행

In [5]:
embedding = tf.Variable(tf.random_normal([vocab_size, embedding_size]), dtype=tf.float32)
embedded_inputs = tf.nn.embedding_lookup(embedding, inputs)

Instructions for updating:
Colocations handled automatically by placer.


세션을 열고 변수들을 초기화

In [6]:
sess = tf.Session()
sess.run(tf.global_variables_initializer())

샘플 인풋 데이터를 정의하고, 임베딩을 수행해서 변형 결과를 확인

In [7]:
input_data = np.array([7])
print("Embedding 전 인풋 데이터: ")
print(sess.run(tf.one_hot(input_data,vocab_size)))
print(tf.one_hot(input_data,vocab_size).shape)
print('Embedding 결과: ')
print(sess.run([embedded_inputs],feed_dict={inputs:input_data}))
print(sess.run([embedded_inputs],feed_dict={inputs:input_data})[0].shape)

input_data = np.array([7,11,67,42,21])
print("Embedding 전 인풋 데이터: ")
print(sess.run(tf.one_hot(input_data,vocab_size)))
print(tf.one_hot(input_data,vocab_size).shape)
print('Embedding 결과: ')
print(sess.run([embedded_inputs],feed_dict={inputs:input_data}))
print(sess.run([embedded_inputs],feed_dict={inputs:input_data})[0].shape)

Embedding 전 인풋 데이터: 
[[0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0.]]
(1, 100)
Embedding 결과: 
[array([[-0.51674426,  0.00487127,  0.84068084,  0.9302916 , -1.8013382 ,
         0.36010912, -0.6714361 , -1.1757022 ,  0.5983085 , -1.510787  ,
        -1.3008538 ,  0.7145155 ,  0.11995181,  1.5791241 ,  1.8553414 ,
        -0.27274016,  0.06851366,  0.28717   ,  0.8271994 ,  0.2263984 ,
        -0.24412726,  0.4041885 , -1.751218  , -0.35375005, -0.5199548 ]],
      dtype=float32)]
(1, 25)
Embedding 전 인풋 데이터: 
[[0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  

유틸리티 함수를 모아놓은 utils 모듈에서 학습 데이터를 읽고 전처리 하기 위한 TextLoader 클래스를 임포트

In [2]:
from utils import TextLoader

학습에 필요한 설정값들을 지정  
RNN의 경우 시계열 데이터를 다루기 때문에 시계열 길이를 나타내는 차원 seq_length 추가

In [4]:
# 학습에 필요한 설정값들을 지정합니다.
data_dir = 'data/tinyshakespeare'
#data_dir = 'data/linux'
batch_size = 50 # Training : 50, Sampling : 1
seq_length = 50 # Training : 50, Sampling : 1
hidden_size = 128   # 히든 레이어의 노드 개수
learning_rate = 0.002
num_epochs = 2
num_hidden_layers = 2
grad_clip = 5   # Gradient Clipping에 사용할 임계값

TextLoader 클래스를 이용해서 학습 데이터를 불러온다.  
학습 데이터에 포함된 모든 단어들을 포함한 List인 Chars 와 id를 부여해 Dictionary 형태로 만든 vocab을 선언

In [5]:
# TextLoader를 이용해서 데이터를 불러옵니다.
data_loader = TextLoader(data_dir, batch_size, seq_length)
# 학습데이터에 포함된 모든 단어들을 나타내는 변수인 chars와 chars에 id를 부여해 dict 형태로 만든 vocab을 선언합니다.
chars = data_loader.chars 
vocab = data_loader.vocab
vocab_size = data_loader.vocab_size # 전체 단어개수

loading preprocessed files


인풋 데이터와 타겟 데이터, 초기 상태값을 입력 받기 위한 플레이스 홀더 선언  
batch_size와 Input Data의 크기인 seq_length로 나중에 치환하기 위하여 None으로서 선언

In [6]:
# 인풋데이터와 타겟데이터, 배치 사이즈를 입력받기 위한 플레이스홀더를 설정합니다.
input_data = tf.placeholder(tf.int32, shape=[None, None])  # input_data : [batch_size, seq_length])
target_data = tf.placeholder(tf.int32, shape=[None, None]) # target_data : [batch_size, seq_length])
state_batch_size = tf.placeholder(tf.int32, shape=[])      # Training : 50, Sampling : 1

Hidden_Layer의 크기는 RNN 마지막 은닉층 출력값을 vocab_size만큼의 소프트맥스 행렬로 변환하기 위한 변수들 설정

In [7]:
# RNN의 마지막 히든레이어의 출력을 소프트맥스 출력값으로 변환해주기 위한 변수들을 선언합니다.
# hidden_size -> vocab_size
softmax_w = tf.Variable(tf.random_normal(shape=[hidden_size, vocab_size]), dtype=tf.float32)
softmax_b = tf.Variable(tf.random_normal(shape=[vocab_size]), dtype=tf.float32)

Instructions for updating:
Colocations handled automatically by placer.


hidden)size(=128) 만큼의 노드 개수를 가진 num_hidden_layers(=2)만큼의 LSTM은닉층들을 cells로 정의

In [8]:
# num_hidden_layers만큼 LSTM cell(히든레이어)를 선언합니다.
cells = []
for _ in range(0, num_hidden_layers):
  cell = tf.nn.rnn_cell.BasicLSTMCell(hidden_size)
  cells.append(cell)

# cell을 종합해서 RNN을 정의합니다.
cell = tf.contrib.rnn.MultiRNNCell(cells, state_is_tuple=True)

Instructions for updating:
This class is equivalent as tf.keras.layers.LSTMCell, and will be replaced by that in Tensorflow 2.0.

For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
If you depend on functionality not listed there, please file an issue.

Instructions for updating:
This class is equivalent as tf.keras.layers.StackedRNNCells, and will be replaced by that in Tensorflow 2.0.


vocab_size 크기의 인풋 데이터를 hidden_size 크기로 임베딩을 수행  
인풋 데이터의 임베딩된 형태인 inputs 변수를 RNN의 입력값으로 사용

In [9]:
# 인풋데이터를 변환하기 위한 Embedding Matrix를 선언합니다.
# vocab_size(One-Hot Encoding 차원) -> hidden_size (Embedded 차원)
embedding = tf.Variable(tf.random_normal(shape=[vocab_size, hidden_size]), dtype=tf.float32)
inputs = tf.nn.embedding_lookup(embedding, input_data)

즉 현재 RNN의 구조를 보게 되면  
Input(batch_size, seq_length) => One-hot-Encoding(vocab size) => Embedding(hidden_size)  
=> Hidden Layer(Hidden Size, Num_Hidden_Size(2))  
=> Softmax Layer(Hidden Size -> Vocab Size)  
가 반복된다는 것을 알 수 있다.  
Num_Hidden_Size(2)는 CNN처럼 문장에서 Feature의 개수 라고 생각할 수 있다.  
Softmax 에서 차원이 늘어나는 이유는 전체 Voacb 중에서 일부를 사용하기 때문이다.    


In [10]:
# 초기 state 값을 0으로 초기화합니다.
initial_state = cell.zero_state(state_batch_size, tf.float32)

# 학습을 위한 tf.nn.dynamic_rnn을 선언합니다.
# outputs : [batch_size, seq_length, hidden_size]
outputs, final_state = tf.nn.dynamic_rnn(cell, inputs, initial_state=initial_state, dtype=tf.float32)
# ouputs을 [batch_size * seq_length, hidden_size] 형태로 변환합니다.
output = tf.reshape(outputs, [-1, hidden_size])

# 최종 출력값을 설정합니다.
# logits : [batch_size * seq_length, vocab_size]
logits = tf.matmul(output, softmax_w) + softmax_b
probs = tf.nn.softmax(logits)

Instructions for updating:
Please use `keras.layers.RNN(cell)`, which is equivalent to this API


- Loss: Softmax_with_loss
- Optimizer: AdamOptimizer

In [11]:
# Cross Entropy 손실 함수를 정의합니다. 
loss = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(logits=logits, labels=target_data))

# 옵티마이저를 선언하고 옵티마이저에 Gradient Clipping을 적용합니다.
# grad_clip(=5)보다 큰 Gradient를 5로 Clipping합니다.
tvars = tf.trainable_variables()
grads, _ = tf.clip_by_global_norm(tf.gradients(loss, tvars), grad_clip)
optimizer = tf.train.AdamOptimizer(learning_rate)
train_step = optimizer.apply_gradients(zip(grads, tvars))

Instructions for updating:

Future major versions of TensorFlow will allow gradients to flow
into the labels input on backprop by default.

See `tf.nn.softmax_cross_entropy_with_logits_v2`.

Instructions for updating:
Use tf.cast instead.


세션을 열고 학습을 진행한다.  
여기서는 아까 과정에서 얘기한  
Input(batch_size, seq_length) => One-hot-Encoding(vocab size)  
을 통하여 현재 InputData를 Embedding 하기 위한 전처리 과정을 진행하는 것을 알 수 있다.

학습이 끝나면, 학습된 파라미터를 이용해서 새로운 문장을 생성하기 위한 샘플링을 진행하게 되는 것을 알 수 있다.  
각각의 샘플링 타입의 특징을 살펴보면 argmax를 취해 정확히 다음에 올 글자를 예측할 수 있지만, 특정 알파벳 이후에는 항상 똑같은 특정 알파벳이 뽑혀서 생성되는 문장의 자유도가 떨어지는 것을 확인 할 수 있다.

In [18]:
# 세션을 열고 학습을 진행합니다.
with tf.Session() as sess:
  # 변수들에 초기값을 할당합니다.
  sess.run(tf.global_variables_initializer())
  
  for e in range(num_epochs):
    data_loader.reset_batch_pointer()
    # 초기 상태값을 초기화합니다.
    state = sess.run(initial_state, feed_dict={state_batch_size : batch_size})

    for b in range(data_loader.num_batches):
      # x, y 데이터를 불러옵니다.
      x, y = data_loader.next_batch()
      # y에 one_hot 인코딩을 적용합니다. 
      y = tf.one_hot(y, vocab_size)            # y : [batch_size, seq_length, vocab_size]
      y = tf.reshape(y, [-1, vocab_size])       # y : [batch_size * seq_length, vocab_size]
      y = y.eval()

      # feed-dict에 사용할 값들과 LSTM 초기 cell state(feed_dict[c])값과 hidden layer 출력값(feed_dict[h])을 지정합니다.
      feed_dict = {input_data : x, target_data: y, state_batch_size : batch_size}
      for i, (c, h) in enumerate(initial_state):
        feed_dict[c] = state[i].c
        feed_dict[h] = state[i].h

      # 파라미터를 한스텝 업데이트합니다.
      _, loss_print, state = sess.run([train_step, loss, final_state], feed_dict=feed_dict)

      print("{}(학습한 배치개수)/{}(학습할 배치개수), 반복(epoch): {}, 손실함수(loss): {:.3f}".format(
        e * data_loader.num_batches + b,
        num_epochs * data_loader.num_batches,
        (e+1), 
        loss_print))

    print("트레이닝이 끝났습니다!")   


  # 샘플링을 시작합니다.
  print("샘플링을 시작합니다!")
  num_sampling = 4000  # 생성할 글자(Character)의 개수를 지정합니다. 
  prime = u' '         # 시작 글자를 ' '(공백)으로 지정합니다.
  sampling_type = 1    # 샘플링 타입을 설정합니다.
  state = sess.run(cell.zero_state(1, tf.float32)) # RNN의 최초 state값을 0으로 초기화합니다.

  # Random Sampling을 위한 weighted_pick 함수를 정의합니다.
  def weighted_pick(weights):
    t = np.cumsum(weights)
    s = np.sum(weights)
    return(int(np.searchsorted(t, np.random.rand(1)*s)))

  ret = prime       # 샘플링 결과를 리턴받을 ret 변수에 첫번째 글자를 할당합니다.
  char = prime      # Char-RNN의 첫번째 인풋을 지정합니다.  
  for n in range(num_sampling):
    x = np.zeros((1, 1))
    x[0, 0] = vocab[char]

    # RNN을 한스텝 실행하고 모델이 예측한 Softmax 행렬을 리턴으로 받습니다.
    feed_dict = {input_data: x, state_batch_size : 1, initial_state: state}
    [probs_result, state] = sess.run([probs, final_state], feed_dict=feed_dict)         

    # 불필요한 차원을 제거합니다.
    # probs_result : (1,65) -> p : (65)
    p = np.squeeze(probs_result)

    # 샘플링 타입에 따라 3가지 종류 중 하나로 샘플링 합니다.
    # sampling_type : 0 -> 다음 글자를 예측할때 항상 argmax를 사용
    # sampling_type : 1(defualt) -> 다음 글자를 예측할때 항상 random sampling을 사용
    # sampling_type : 2 -> 다음 글자를 예측할때 이전 글자가 ' '(공백)이면 random sampling, 그렇지 않을 경우 argmax를 사용
    if sampling_type == 0:
      sample = np.argmax(p)
    elif sampling_type == 2:
      if char == ' ':
        sample = weighted_pick(p)
      else:
        sample = np.argmax(p)
    else:
      sample = weighted_pick(p)

    pred = chars[sample]
    ret += pred     # 샘플링 결과에 현재 스텝에서 예측한 글자를 추가합니다. (예를들어 pred=L일 경우, ret = HEL -> HELL)
    char = pred     # 예측한 글자를 다음 RNN의 인풋으로 사용합니다.

    print("샘플링 결과:")
    print(ret)

0(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 4.886
1(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 4.027
2(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 3.906
3(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 3.807
4(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 3.493
5(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 3.469
6(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 3.336
7(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 3.273
8(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 3.282
9(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 3.239
10(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 3.149
11(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 3.111
12(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 3.079
13(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 3.029
14(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 2.986
15(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 2.912
16(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(los

137(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.921
138(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.908
139(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.913
140(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.909
141(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.902
142(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.875
143(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.897
144(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.907
145(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.858
146(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.903
147(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.916
148(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.915
149(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.903
150(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.964
151(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.938
152(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.965
153(학습한 배치개수)/924(학습할 배치

272(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.741
273(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.696
274(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.722
275(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.707
276(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.733
277(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.646
278(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.694
279(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.701
280(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.732
281(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.735
282(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.761
283(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.661
284(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.699
285(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.772
286(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.709
287(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.728
288(학습한 배치개수)/924(학습할 배치

407(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.627
408(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.681
409(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.720
410(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.750
411(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.617
412(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.595
413(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.585
414(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.573
415(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.609
416(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.597
417(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.624
418(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.636
419(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.611
420(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.549
421(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.604
422(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 1, 손실함수(loss): 1.600
423(학습한 배치개수)/924(학습할 배치

542(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.529
543(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.531
544(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.521
545(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.603
546(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.531
547(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.599
548(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.603
549(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.550
550(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.564
551(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.556
552(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.598
553(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.516
554(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.476
555(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.515
556(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.506
557(학습한 배치개수)/924(학습할 배치개수), 반복(epoch): 2, 손실함수(loss): 1.505
558(학습한 배치개수)/924(학습할 배치

...

샘플링 결과:
 slawbles
Which are our mornione habkehford, here bushwind!
Bad you nexcetio blood!
Gvold him severcous at so, but that fellow'd,
exeched, gold ofter. Tho sate of each her thile,
What have I am will our made me longd?

TRANIO:
Come, dolder, his not dow, how impil;
Marsay, not the partia on the tranchidy.
And for deed, among thyself; and alcors for age
Gracenit asmose overdician he should bound
Moy't towelf, and that let thy live
Onued that to a cruched to our had, if each,
Be by my se'er! you never burhed, slecteds;
This your Iracher?

BAAPTISTA:
Let to me her. There is an agains no soundly.
I made diughts' be glace to no leation.
Is millour's have now. Let of us go suse, he
mow comfortt, I have her sound son him,
And, kiss as thing your falpers for if scarched:
Moraful sown hechard viration to humble courtses;
Now seil that did five hath and pather!

TRANIO:
Think Warrwase him: he shall York. Why, I will that
me I dost be that these what imasted this camas?
Whatchese is my lud

샘플링 결과:
 slawbles
Which are our mornione habkehford, here bushwind!
Bad you nexcetio blood!
Gvold him severcous at so, but that fellow'd,
exeched, gold ofter. Tho sate of each her thile,
What have I am will our made me longd?

TRANIO:
Come, dolder, his not dow, how impil;
Marsay, not the partia on the tranchidy.
And for deed, among thyself; and alcors for age
Gracenit asmose overdician he should bound
Moy't towelf, and that let thy live
Onued that to a cruched to our had, if each,
Be by my se'er! you never burhed, slecteds;
This your Iracher?

BAAPTISTA:
Let to me her. There is an agains no soundly.
I made diughts' be glace to no leation.
Is millour's have now. Let of us go suse, he
mow comfortt, I have her sound son him,
And, kiss as thing your falpers for if scarched:
Moraful sown hechard viration to humble courtses;
Now seil that did five hath and pather!

TRANIO:
Think Warrwase him: he shall York. Why, I will that
me I dost be that these what imasted this camas?
Whatchese is my lud

샘플링 결과:
 slawbles
Which are our mornione habkehford, here bushwind!
Bad you nexcetio blood!
Gvold him severcous at so, but that fellow'd,
exeched, gold ofter. Tho sate of each her thile,
What have I am will our made me longd?

TRANIO:
Come, dolder, his not dow, how impil;
Marsay, not the partia on the tranchidy.
And for deed, among thyself; and alcors for age
Gracenit asmose overdician he should bound
Moy't towelf, and that let thy live
Onued that to a cruched to our had, if each,
Be by my se'er! you never burhed, slecteds;
This your Iracher?

BAAPTISTA:
Let to me her. There is an agains no soundly.
I made diughts' be glace to no leation.
Is millour's have now. Let of us go suse, he
mow comfortt, I have her sound son him,
And, kiss as thing your falpers for if scarched:
Moraful sown hechard viration to humble courtses;
Now seil that did five hath and pather!

TRANIO:
Think Warrwase him: he shall York. Why, I will that
me I dost be that these what imasted this camas?
Whatchese is my lud

샘플링 결과:
 slawbles
Which are our mornione habkehford, here bushwind!
Bad you nexcetio blood!
Gvold him severcous at so, but that fellow'd,
exeched, gold ofter. Tho sate of each her thile,
What have I am will our made me longd?

TRANIO:
Come, dolder, his not dow, how impil;
Marsay, not the partia on the tranchidy.
And for deed, among thyself; and alcors for age
Gracenit asmose overdician he should bound
Moy't towelf, and that let thy live
Onued that to a cruched to our had, if each,
Be by my se'er! you never burhed, slecteds;
This your Iracher?

BAAPTISTA:
Let to me her. There is an agains no soundly.
I made diughts' be glace to no leation.
Is millour's have now. Let of us go suse, he
mow comfortt, I have her sound son him,
And, kiss as thing your falpers for if scarched:
Moraful sown hechard viration to humble courtses;
Now seil that did five hath and pather!

TRANIO:
Think Warrwase him: he shall York. Why, I will that
me I dost be that these what imasted this camas?
Whatchese is my lud

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

